In [55]:
# ####################################### SET PARAMETERS ####################################

area_key = "Area um^2"
tracer_key = "Num AF647"
marker = "CFos"


# ###########################################################################################

normalization = "RelativeDensity"
min_animals_cross_correlation = None
plot_regions_with_insufficient_data = False
p_cutoff = 0.05
r_cutoff = 0.9

In [2]:
import BraiAn
import os

In [3]:
# SOUMNYA FEMALES+MALES - 2 Groups {Stress|Control}
experiment = "soumnya"
groups = [
    "Control",
    "Stress"
]
plots_output_folder = "C-S"

In [ ]:
# SOUMNYA ALL - 2 Groups {Stress|Control} + 2 Groups {Males|Females}
experiment = "soumnya"
groups = [
    "Control (Females)",
    "Stress (Females)",
    "Control (Males)",
    "Stress (Males)"
]
plots_output_folder = "CF-SF-CM-SM"

In [ ]:
# SOUMNYA FEMALES - 2 Groups {Stress|Control}
experiment = "soumnya"
groups = [
    "Control (Females)",
    "Stress (Females)",
]
plots_output_folder = "CF-SF"

In [31]:
# SOUMNYA MALES - 2 Groups {Stress|Control}
experiment = "soumnya"
groups = [
    "Control (Males)",
    "Stress (Males)"
]
plots_output_folder = "CM-SM"

In [ ]:
# SHILA - 3 Groups {Control|Stress|Resilient}
experiment = "shila"
groups = [
    "Control",
    "Stress",
    "Resilient"
]
plots_output_folder = "C-S-R"

In [ ]:
# SHILA - 2 Groups {Control|Stress+Resilient}
experiment = "shila"
groups = [
    "Control",
    "Stress"
]
plots_output_folder = "C-S"

In [ ]:
# TEST DATA - Sample data
experiment = "test"
groups = [
    "Control",
    "Stress",
    "Resilient"
]
plots_output_folder = "C-S-R"

In [32]:
animals_root = f"./data/experiments/{experiment}/QuPath_output/"
data_input_path = f"./data/experiments/{experiment}/BraiAn_norm_output/"
plots_output_path = f"./plots/{experiment}/{plots_output_folder}"

if not(os.path.exists(plots_output_path)):
    os.makedirs(plots_output_path, exist_ok=True)

In [33]:
animal_groups = [BraiAn.AnimalGroup.from_csv(group, data_input_path, f"results_cell_counts_{group}.csv") for group in groups]

In [34]:
# from https://help.brain-map.org/display/api/Downloading+an+Ontology%27s+Structure+Graph
# StructureGraph id=1
path_to_allen_json = "./data/AllenMouseBrainOntology.json"

branches_to_exclude = ["retina", "VS", "grv", "fiber tracts", "CB"]
AllenBrain = BraiAn.AllenBrainHierarchy(path_to_allen_json, branches_to_exclude)
AllenBrain.select_from_csv("./data/AllenSummaryStructures.csv")

In [35]:
# low_threshold = 700 # Only plot bars with value larger than threshold
# top_threshold = 4_000 # np.inf
# regions_to_plot = BraiAn.regions_to_plot(groups=animal_groups, normalization=normalization, low_threshold=low_threshold, top_threshold=top_threshold)
regions_to_plot = AllenBrain.get_selected_regions() # selects the Summary Strucutures

In [53]:
groups_cross_correlations = []
for group in animal_groups:
    r, p = group.cross_correlation(normalization, regions_to_plot, min_animals=min_animals_cross_correlation)
    if not plot_regions_with_insufficient_data:
            r.dropna(axis=0, how="all", inplace=True)
            r.dropna(axis=1, how="all", inplace=True)
            p.dropna(axis=0, how="all", inplace=True)
            p.dropna(axis=1, how="all", inplace=True)
    groups_cross_correlations.append((r, p))

In [56]:
for group, (r,p) in zip(animal_groups, groups_cross_correlations):
    # group_1_plot_filename = f"cross_correlation_{marker}_{normalization}_{group_1_plot_name}.svg"
    # group_1_plot_filepath = os.path.join(plots_output_path, group_1_plot_filename)
    group_1_plot_filepath = None
    fig = BraiAn.plot_cross_correlation(r, p, filename=group_1_plot_filepath, cell_height=5)
    fig.show()

In [57]:
for group, (r,p) in zip(animal_groups, groups_cross_correlations):
    fig = BraiAn.draw_chord_plot(r, p, r_cutoff, p_cutoff, AllenBrain,
                                ideograms_a=50,
                                title=f"{group.name} connectomics graph from Pearson correlation (|r| >= {r_cutoff}, p >= {p_cutoff})",
                                size=1200,
                                no_background=False,
                                annotation1="This is the first annotation",
                                annotation2="This is the second annotation",
                                annotation3="This is the third annotation")
    fig.show()

In [46]:
fig = BraiAn.plot_groups(normalization, AllenBrain, *animal_groups,
                            selected_regions=regions_to_plot, use_acronyms=False, height=10_000)

file_title = f"barplot_{animal_groups[0].marker}_{normalization}_{len(animal_groups)}groups.png"
fig.write_image(os.path.join(plots_output_path, file_title))
# fig.show()